In [1]:
import nltk
from nltk.tokenize import word_tokenize
from nltk.stem.snowball import EnglishStemmer
from nltk.corpus import words, stopwords

import keras
import pandas as pd
import numpy as np

from keras.preprocessing import text, sequence
import gensim.models.word2vec as w2v
import copy
from tqdm import tqdm
import multiprocessing as mp

import re
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import SnowballStemmer

from string import maketrans 

Using TensorFlow backend.


In [2]:
train = pd.read_csv("./train_cleaned.csv")
test = pd.read_csv("./test_cleaned.csv")

In [74]:
re.sub('(s(h|\*)(i|\*)(t|\*))', 'shit', "s****ing")

'shit*ing'

In [9]:


def clean_text(text):
    
    # Convert words to lower case and split them
    text = text.lower()
    
    text = re.sub(r'[^\x00-\x7F]',' ', text)
    text = re.sub(r'\[(.*)_link:.*\]',re.IGNORECASE)

    
    # Clean the text
    text = re.sub(r"what's", "what is ", text)
    text = re.sub(r"\'s", " ", text)
    text = re.sub(r"\'ve", " have ", text)
    text = re.sub(r"can't", "cannot ", text)
    text = re.sub(r"n't", " not ", text)
    text = re.sub(r"i'm", "i am ", text)
    text = re.sub(r"'m", " am ", text)
    text = re.sub(r"\'re", " are ", text)
    text = re.sub(r"\'d", " would ", text)
    text = re.sub(r"\'ll", " will ", text)
    text = re.sub(r",", " ", text)
    text = re.sub(r"\.", " ", text)
    text = re.sub(r"!", " ! ", text)
    text = re.sub(r"\/", " ", text)
    text = re.sub(r"\^", " ", text)
    text = re.sub(r"\+", " ", text)
    text = re.sub(r"\-", " ", text)
    text = re.sub(r"\=", " ", text)
    text = re.sub(r"'", " ", text)
    text = re.sub(r"(\d+)(k)", r"\g<1>000", text)
    text = re.sub(r":", " ", text)
    text = re.sub(r" e g ", " eg ", text)
    text = re.sub(r" b g ", " bg ", text)
    text = re.sub(r" u s ", " american ", text)
    text = re.sub(r"\0s", "0", text)
    text = re.sub(r" 9 11 ", "911", text)
    text = re.sub(r"e - mail", "email", text)
    text = re.sub(r"j k", "jk", text)
    text = re.sub(r"\s{2,}", " ", text)
    
    text = text.split()
    
    stops = set(stopwords.words("english"))
    text = [w for w in text if not w in stops]
    
    stemmer = SnowballStemmer('english')
    stemmed_words = [stemmer.stem(word) for word in text]
    text = " ".join(stemmed_words)
    
    return(text)

In [4]:
print(train.shape)
print(test.shape)

(95851, 8)
(226998, 2)


In [10]:
#all_text = test["comment_text"].dropna().values
#all_text = list(np.append(all_text, train["comment_text"].dropna().values))
#all_text_clean = [""]*len(all_text)
#for i in tqdm(range(len(all_text))):
#    all_text_clean[i] = text_to_wordlist(all_text[i])
#all_text_tokenized = [word_tokenize(s) for s in all_text_clean]
#print len(all_text)
#print len(all_text_tokenized)


list_sentences_train = train["comment_text"].fillna("CVxTz").values
list_classes = ["toxic", "severe_toxic", "obscene", "threat", "insult", "identity_hate"]
y = train[list_classes].values
list_sentences_test = test["comment_text"].fillna("CVxTz").values

for i in tqdm(range(len(list_sentences_train))):
    list_sentences_train[i] = clean_text(list_sentences_train[i])
    
for i in tqdm(range(len(list_sentences_test))):
    list_sentences_test[i] = clean_text(list_sentences_test[i])
    



100%|██████████| 226998/226998 [03:25<00:00, 1104.30it/s]


In [15]:
def count_words(corpus):
    word_counts = {}
    for sentence in corpus:
        for word in set(sentence.split()):
                if word not in word_counts: word_counts[word] = 0
                word_counts[word] += 1
    return word_counts

all_text = list(list_sentences_train) + list(list_sentences_test)
print len(all_text)
word_counts = count_words(all_text)

322849


In [37]:
print len(word_counts)
val_words = set()
for k, v in word_counts.items():
    if v > 1:
        val_words.add(k)
    else:
        print k

174751
userrinpochemari
cwrtnewydd
wwwpubmedgov
spiderl
utnapishtim
crucifer
franglifri
vinalop
popunjavati
coccinioid
dekolb
scmzzzzzzz
nordisk
autochthonousresid
lench
proximaalpha
alwiqi
jcdenton
jairam
brontother
eduemoni
fisheriesmgmt
monthnam
rickman
ammassalik
nazietc
wikipediaaccept
workto
analucia
knowledgejpg
connorsjpg
wwwentertainmentwisecomnewsid
nusranot
focusoninfin
articlesonneolog
inapropi
imagehbmeiahjpg
hanastop
statlig
wikilov
chongguadalok
strummercashredemptionsongogg
tilton
sockpuppetingno
imagetomgeorgejpeg
khahand
filedohertyjpg
metadragonfir
bouchervill
nonbrit
talkttnarch
nanjungudu
longip
jimlewisjr
inkster
azerbaijanazerbaijan
hayreddin
gormaz
terhadap
arachakravarthi
imagejacintaaajpg
unknownunknownromania
ragemanchoo
bebutrtjgfjkghjhlgskghhfgjkwalebnjk
templarion
cazzat
satellitephonestor
herbag
borgwarn
daftar
questionnaireconstructiontypesofquest
targa
yeunga
tumen
arizonausa
psivalt
devam
tishthati
gayyyyyyyyyyy
urrrppp
sdtv
alllll
sagakanon
frozengren

llangurig
cyclesformatrixmultipl
chaathira
nomshtr
badastronomercom
adroid
stornoway
tritomex
ginunt
technicalcheckus
richardveryard
imagealisonbechdeljpg
foregin
tawkerbottawkerbot
yesss
mresolutionlicens
iolo
imageshinhwastateoftheartjpg
timeous
fqngfdbfggbnfsdmlsmmfdknhknknknkbkb
mmmmye
portlandand
matsunaga
itwikipediaorgwikimarieluv
slaviclanguag
talkgreatestrowerev
koszegi
poerel
laahu
wpanpropos
digitalspi
nonstatist
bushrangerth
talkadriano
pentylnaphthoylindol
graaf
graag
padmanabhan
borek
wpprimaryusag
hochberg
extenenwiki
existnonpow
mpv
wanr
storstockholm
lucen
lucem
usergeorgiawikiwrit
vanhoabui
nykkjen
autel
locklear
cryptosupersession
olsa
gaysorbi
ubereffici
oyigudsfghklj
imageslashtmntgif
coverpl
bektasi
proswansea
lumpish
posedeia
rossa
redlinksnolink
rasputrajpga
seirawan
trapperswolf
silverhilldal
kaupth
windflow
diagraphia
vaejah
sarveroygevalt
heenan
polysorb
kakinuma
goofwrak
barbarasu
barfight
angelomatistsougaraki
sarit
brgyud
randrangei
pahapaha
islandssan
han

tmthtemail
stroessner
talkorson
specialemailuserhuntst
imagelogocjpg
liesntn
fust
verecundium
jujubefuck
stiefzust
mbuidhin
askpolitelyrath
perikaperika
ldiein
postabl
pushrod
talkchelicerataga
ballclub
baitandswitch
belarusfilm
albaqara
averyindex
entwisl
ehkenwiki
mizer
guenon
tailback
sansar
daler
imagemesolonghijpg
nvnv
israr
notsobright
mactograph
pennywhistl
lepanto
kombetar
desript
nairanil
srslyon
changeremoverevert
metatalk
greekhalf
thankz
dorff
togepi
gmboxtodayequivalphac
mccreanor
mwahahahahaha
wayyyyyi
judaismexclus
sabica
carnahan
anyher
isral
wikipediaadministratorsmisuseofadministrativetool
sechski
disini
extragalact
talkgalvestonbayareasourcesor
reviewchessarch
summand
ricordi
blindest
disint
cheersjetlov
filemondoglobo
sasan
kavignar
suced
espana
malljaja
worstest
carnival
volunteersnumvolunt
bomen
sweptawayjpg
caricom
josephsimplehtml
tdjpg
fileanastacia
sixx
childbear
welcommitte
rentacop
talkomegapointtiplerdisruptiveeditingbytimshuba
shroudofturin
supeliga
wikipe

censorshipmeist
strepsiadi
lalejin
endicott
solkoff
wikipediauploadingimagestechnicalaspect
technofay
cinchona
weidenreich
leeroy
persondatapleas
portraitsmjpg
diplomata
blive
simpsonsinv
elwynn
eyepiec
sparepart
shadowbrookspiff
mfacebookcomdibashthapathank
dancersingeractressand
cenr
cens
heteroflex
wikipediaexampl
monitori
twitaiwan
filevoluntaryismpng
everkorsentri
cenk
yutsun
homecom
hahahathough
strawbal
happin
balsamiq
rdcst
tthat
ststephensor
imageadamsawlawrencejpg
nollywood
hayyyyyyyyy
workfar
skaldic
llibertat
meneklt
despojar
sbmorg
jiz
sabun
districtisrael
heaton
amm
manchesterbolton
milker
sleepyhead
enkel
heriberto
fileromstbenjpg
pinganthoni
ekin
ekil
pericana
curtiusrufus
aml
prediscuss
youdid
shecher
ensiform
fatoumandelbrot
gablehaus
afficionado
lws
gregnorc
anom
xanarki
juhuri
munavvar
utrikesdepartementet
useradijapan
southeastasian
witzeman
jahiegel
shesaid
imageholm
boupai
usermanav
lithuaniarel
carpocr
xtremedood
roulettedatedecemb
haglazhaglan
fileurbandubjpg
a

congametrail
rsmmc
gedhun
opolskiego
pleawikipedia
hhvfhyrfuusigtuirtiiccdjkcfidfidififioidieijmjbnm
gamesrockstar
wwwpwinsidercom
medkit
layamon
talktexted
userslythefox
saidvassallo
ulkhwarazm
henreittapussycat
intstead
prematch
hieraaetusaquila
erekatstat
sres
parineeta
usefulsalim
nanomesh
filegenisjpg
ejnar
afghanistanbaloachistan
znamya
rendelkez
antioxfordian
berkovitz
honeynet
unalign
mimsywhomev
uswest
iberica
geailg
fibrosarkoma
imageosmanbirsenjpg
biasa
swinnertondy
wikispecieswikinew
usercoolcaesar
bartmuni
talkstoneag
oneaftertheoth
imagegotthethirstjpg
goodnaturedbutwrong
suffient
toddsmustang
imagecataniajpg
wpfilmnfi
liketh
liketo
pemigewasset
ubiq
openmotif
misyonumuzu
lectio
lectin
langdialect
fitjpgjpg
imagemartarailmapjpg
mootmootmootmootmootmootmootmootmootmoot
sourquoi
alexaobriencom
toyohara
usermilliot
kaliabor
stonecutt
mydopumpin
paintthinnersnif
imagecaselogojpg
imagefnlaflaggif
powstaczego
histnat
winnacunnet
paleogen
givenweisjusija
mudpit
filepanten
notice

...

olyfaunt
ukraineborn
giselalisa
rfclulu
venezuelarel
wikipediarequestsforarbitrationcizevid
patientandfriend
gabrielino
oranjenassau
wikipediabarclay
angelesdomin
menyenangkan
rundgrend
comman
bayerisch
livedvdjpg
spielbeziehungen
khilaaf
conceren
jhubsph
prequisit
heindel
americakorean
alieva
rosterholla
dtabmoney
rntalkcomubbthreadsshowflatphpboarddvdtalknumb
laffey
dieselpunk
antigmo
hizzl
superquick
natio
sebadoh
meamiorg
electroconduct
specialemailuserblu
nunquam
himlen
imageadelestephensjpg
userpatricknoddi
baffel
talkroyalcoatofarmsoftheunitedkingdomwilliamandmari
arrier
pourront
nonchasidim
imagehiraijpg
hobbler
xtkcosf
gelo
ixnay
cenerentola
jennaveccia
urduhindi
castlejpg
cameria
tangenc
imagesylviawatsoncampaignjpg
faggotschan
merrittbrown
ricegrass
nawanshehrdirector
zeffirellijpg
reinga
stadtzeitung
kalanilyam
aedicula
wkend
oyama
firmest
envoirmentbut
fontweightboldtextaligncenterattent
lijealso
theoreticalusha
languagesandmost
engem
hedera
ripperologist
broderbund
gmaxw

talkyellowjacket
muslimsarabsegyptian
imagethurmanbridejpg
wikipediaadministratorsnoticeboardincidentsjjj
idda
dasakuta
proceess
begintemplatedocexamplet
fellgett
imagepeasantsquestmoviejpg
wetnurs
understandanywayto
jazzcatevolut
wpolitycepl
kaseki
templatekshatriya
addedromero
morgannwg
sspecialprefixindeximagebookkeep
imani
botmeist
backtobas
filetincin
abvious
llibr
turnhouttilburg
wikipedianotabilitybookscriteria
fazem
barbarasanta
wpanuserjamesmlan
bhala
lauriston
deletionfay
bieksa
eeer
characterless
filecroatiandialectspng
jrb
realesana
calama
moonbas
mcmilesfan
johoreon
alyea
userffa
sciencehitechreview
tael
anticlimax
colaborador
offensiveamnon
ramijuddin
imagelazarocardenasjpg
vapaaehtoinen
microsurg
neurophenomenologycom
arvikar
imagerhythmboxpng
receptionjam
fbovallen
talknord
semivaporizermayb
yeahhhhhhhhhhhh
pphpd
trichoman
jhangkhanewalvehari
admeadit
fgif
calcebuef
lincolnsuggest
esmiki
uuhh
syscon
knowledgetimeheart
drvictorvondoom
ancestryfuckoffjewish
hvalac
lfiafri

assholr
hypothosi
interculturalidad
swazilandfiji
busyconina
diannatelesburtalbert
mahmudiyah
versechorusvers
macculloch
raresheid
geraci
imagebattlelor
vlachika
dromaeosaurid
semannesir
noterairti
userlyinginbedmon
wikipediadidyouknowstatist
filegcalexanderjpg
cuccu
enterprisedashboardcom
imagelbjjpg
chabrus
mentallystuptard
yardlin
peirrehenri
wikipediatemplatesfordeletiontemplatevideo
mazing
youknowit
imagegreatestptijpg
kusanagi
jemal
imagegantzkuronogif
eropa
wittfogel
suckleymapl
mandibl
marekspiff
raglan
centgeorg
kunnapatti
boulderopoli
phpsampleh
coinstar
disiplin
usertalkbangabalunga
battlemech
mohistorybuff
wpspamsourc
kohaku
closestopshut
alekseevich
cloaksirc
wpucga
imagemaxheadroommpegmanjpg
mkarunanidhi
paediatricianusa
kvrlkdogkriv
vladimirnovna
internetbooksvoic
fishmong
glebov
ernoskosti
gavrilo
anisotrop
dhere
cruch
autocorrel
krushodari
smallcapsmsc
revoic
imagetitanicdvdjpg
geohumphrey
freien
vitterrfc
freier
fanout
jdebaet
filezomergemlocatiepng
gagu
leafag
michol

westernhagen
yasar
changez
talkbungholiooo
placin
jaleel
loosethehotbutton
nistrov
zippiti
blowtorch
imagedipjpg
forumi
wikipediawikicuphistorysubmissionshawkey
yesaffirmativegreen
klsdjfhsdlkjfhsdjklfh
szentgyorgyi
chametz
phalerist
crombi
reputationkaikolar
banneduncitedplagiaris
maceoin
postojalo
kalyanaraman
kummer
niin
imageezpinosapng
sebastkk
cznsgjpg
assen
arameansyriac
svwikipediadet
assez
pillowfight
ayoubmalouk
ctrlrefresh
slavmacedonian
minnekhada
gamelik
vangard
hopefullyenshallah
bradluagh
tampo
arseup
talkcircumcisionarch
uklocalnorthwest
kemungkinan
porijekla
totilo
sereth
nowsteven
iskongaudiya
atassi
adebayo
hystat
nottoodubioussound
joolz
counterflow
armhol
spys
obstojea
wyka
uteg
servicedestinationfrequencyjourney
pegarnejemplon
yevpati
coloursa
tyrannosauroidea
neshk
khodorkovskiyuko
anyodi
talkmustafa
bunc
bune
talkstrothra
usedkakit
buno
woogoszcz
thrunigowa
mrselfishass
lordycousin
rajgopalachari
nonsingular
sentenceineacharticl
martinusvanschalkwyk
oppisit
info

sethlit
ecout
sreedhara
imagepapastathopoulosjpg
managementaitam
hassanali
ninwiki
danz
companionsmediaspecif
illequip
unblockedhoweverth
dand
scnwiktionari
danb
grnyrosiko
spectrograph
resuperheat
totallydisputeddatejun
futhurhav
saraceno
galg
importn
manjooran
inadna
dedid
protoital
winfr
publicforal
sabaton
periodont
usertalkkmccoydelfino
ayudhajivi
nadyb
talkgoogiearchitecturechristchurch
santafe
dalmadaldala
mattoso
probibl
imageasanzpng
dennisfeinstein
overwis
imagenatebarcalowjpg
pdfbot
panurgel
drogba
ferroelectr
heterosex
visionandpsychosisnet
unvail
belowamsa
formattingsscriptmosnum
wwwoxfordshakespearecomdocumentshtml
aldirmagonul
enstrm
userdesiegeltest
gazpromavia
bygif
livestream
historicalculturalreligi
fileuniverseglyphjpg
nagara
fong
chieftainci
punchandjudi
wikinewb
ekstensif
ludbut
alreadykrystaleen
canaentab
slytherin
berulangulang
vandenbergarch
stegner
wikipediaunusu
corralito
turkopersia
imageelpng
sunnybrook
esporsi
cholapallava
spefic
hornswogglechavo
babeland


In [36]:
print len(val_words)

69946


In [43]:
def remove_low_freq_words(text, val_w):
    text = text.split()
    text = [w for w in text if w in val_w]
    text = " ".join(text)
    return text

for i in tqdm(range(len(list_sentences_test))):
    list_sentences_test[i] = remove_low_freq_words(list_sentences_test[i], val_words)


100%|██████████| 226998/226998 [00:02<00:00, 78422.91it/s]


In [44]:
print len(list_sentences_test)

226998


In [41]:
len(" ".join([]))

0

In [47]:
i = 0
for l,s in enumerate(list_sentences_test):
    if len(s)==0:
        i += 1
        print l
print i

12
41
47
53
56
105
670
1093
1108
1316
1602
1688
1985
2291
2375
2381
2415
2454
2456
2848
3277
3378
3434
3473
3484
3537
3552
3941
3976
4008
4661
4704
4764
4876
4961
5088
5167
5453
5561
5594
5823
6209
6442
6561
6604
6610
6615
6680
6993
7304
7571
7944
8007
8084
8526
8847
8894
8930
9122
9148
9545
9567
9632
9712
9836
9870
9949
10124
10407
10447
10730
10770
11210
11305
11332
11383
11486
11505
11694
11894
12011
12607
12982
13047
13048
13087
13123
13146
13203
13217
13246
13363
13442
13757
13787
13868
14000
14101
14194
14314
14536
14665
14766
14825
14863
15058
15222
15279
15312
15390
15450
15467
15540
15692
16038
16062
16434
16694
16719
16872
16962
16972
17168
17547
17696
17757
18005
18422
18544
18743
18874
18956
19241
19330
19380
19493
19553
19698
19702
19998
20018
20025
20447
20513
20864
20940
21019
21228
21269
21532
21547
21681
21731
21812
21828
22028
22268
22293
22567
22573
22593
22639
22877
23100
23295
23441
23463
23492
23563
23744
23839
23863
23908
23989
24189
24192
24426
24431
24505
24561

In [51]:
print test.iloc[4008]

id              17739820297
comment_text              a
Name: 4008, dtype: object


In [46]:
1631.0/226998

0.007185085331148292

In [27]:
word_counts['chongguadalok']

1

In [41]:
tokenizer = text.Tokenizer(num_words=max_words)
tokenizer.fit_on_texts(list(list_sentences_train) + list(list_sentences_test))
word_index = tokenizer.word_index
print('Found %s unique tokens' % len(word_index))

list_tokenized_train = tokenizer.texts_to_sequences(list_sentences_train)
list_tokenized_test = tokenizer.texts_to_sequences(list_sentences_test)
X_t = sequence.pad_sequences(list_tokenized_train, maxlen=maxlen)
X_te = sequence.pad_sequences(list_tokenized_test, maxlen=maxlen)

Found 220243 unique tokens


In [42]:
list_tokenized_train[0]

[771, 2076, 269, 7863, 43, 6, 177, 8, 324, 6, 36, 16, 22, 310, 12665]

In [51]:
list_tokenized_all = list_tokenized_train + list_tokenized_test
for i in tqdm(range(len(list_tokenized_all))):
    list_tokenized_all[i] = map(str, list_tokenized_all[i])

100%|██████████| 322849/322849 [00:05<00:00, 59450.74it/s]


In [53]:
list_tokenized_all[0]

['771',
 '2076',
 '269',
 '7863',
 '43',
 '6',
 '177',
 '8',
 '324',
 '6',
 '36',
 '16',
 '22',
 '310',
 '12665']

In [44]:
print len(list_tokenized_test)
print len(list_tokenized_train)
print len(list_tokenized_all)

226998
95851
322849


In [114]:
# hyper parameters of the word2vec model
num_features = 300 # dimensions of each word embedding
min_word_count = 10 # this is not advisable but since we need to extract
# feature vector for each word we need to do this
num_workers = mp.cpu_count() # number of threads running in parallel
context_size = 7 # context window length
downsampling = 1e-3 # downsampling for very frequent words
seed = 1 # seed for random number generator to make results reproducible
num_iter=1

In [115]:
word2vec_ = w2v.Word2Vec(
    sg = 1, seed = seed,
    workers = num_workers,
    size = num_features,
    min_count = min_word_count,
    window = context_size,
    sample = downsampling
)

In [116]:
# first we need to built the vocab
word2vec_.build_vocab(list_tokenized_all)

In [117]:
print word2vec_.iter

5


In [118]:
word2vec_.train(list_tokenized_all, total_examples = word2vec_.corpus_count, epochs = word2vec_.iter)

70340091

In [119]:
for i, k in word_index.items():
    if k == 5666: print i

ullmann


In [126]:
word_index['bms']

53832

In [128]:
word2vec_.wv.most_similar('53832')

KeyError: "word '53832' not in vocabulary"

In [127]:
nums = set([])
for num, value in word2vec_.wv.most_similar('53832'): nums.add(num)

print nums
    
for i, k in word_index.items():
    if str(k) in nums: print i

KeyError: "word '53832' not in vocabulary"

In [124]:
len(word2vec_.wv.vocab)

37368

In [28]:
MAX_SEQUENCE_LENGTH = 150
max_words = 100000
maxlen = 150

VALIDATION_SPLIT = 0.1

from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences


list_sentences_train = train["comment_text"].fillna("CVxTz").values
list_classes = ["toxic", "severe_toxic", "obscene", "threat", "insult", "identity_hate"]
y = train[list_classes].values
list_sentences_test = test["comment_text"].fillna("CVxTz").values

for i in tqdm(range(len(list_sentences_train))):
    list_sentences_train[i] = text_to_wordlist(list_sentences_train[i])
    
for i in tqdm(range(len(list_sentences_test))):
    list_sentences_test[i] = text_to_wordlist(list_sentences_test[i])
    

tokenizer = text.Tokenizer(num_words=max_words)
tokenizer.fit_on_texts(list(list_sentences_train) + list(list_sentences_test))
word_index = tokenizer.word_index
print('Found %s unique tokens' % len(word_index))

list_tokenized_train = tokenizer.texts_to_sequences(list_sentences_train)
list_tokenized_test = tokenizer.texts_to_sequences(list_sentences_test)
X_t = sequence.pad_sequences(list_tokenized_train, maxlen=maxlen)
X_te = sequence.pad_sequences(list_tokenized_test, maxlen=maxlen)


100%|██████████| 226998/226998 [00:18<00:00, 12234.95it/s]


Found 220243 unique tokens


In [30]:
print len(word2vec_.wv.vocab)

220236


In [14]:
print X_te[0]

[   0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0 1109  525  217 4100 2648]


In [34]:
word2vec_.wv.most_similar('bme')


[('mandatorially', 0.8621666431427002),
 ('electrochemistry', 0.8616641759872437),
 ('disapora', 0.8576161861419678),
 ('garnishes', 0.8563162088394165),
 ('chrystal', 0.8549282550811768),
 ('deseases', 0.8520304560661316),
 ('cladograms', 0.8511778116226196),
 ('drumlin', 0.8493999242782593),
 ('revolutionizing', 0.8479541540145874),
 ('dermatological', 0.8476134538650513)]

In [36]:
'bms' in word2vec_.wv.vocab

True

In [32]:
nb_words = max(max_words, len(word_index))+1

embedding_matrix = np.zeros((nb_words, EMBEDDING_DIM))
for word, i in word_index.items():
    print word
    if word in word2vec_.wv.vocab:
        embedding_matrix[i] = word2vec_.wv.word_vec(word)
print('Null word embeddings: %d' % np.sum(np.sum(embedding_matrix, axis=1) == 0))

ftdna
tsukino
vang
nunnery
sowell
utnapishtim
hanastop
vinalop
woods
clotted
spiders
dekolb
ultimatley
woody
trawling
comically
kalmar
kosekjpg
regularize
canes
jcdenton
sprague
caney
jairam
acurately
supasoldier
igual
caned
accpetance
harbhajanponting
mivie
rickman
missionizing
touristed
naturopathic
connorsjpg
swornwyvren
grenadiers
pigment
imagehbmeiahjpg
asianpacific
comptuer
bringing
imgimagesha
prizing
jrpg
weell
munichgermany
wooded
grueling
khahand
wooden
wholemeal
wednesday
virtuosos
animosities
createdmcintire
elgar
amplifications
immunities
jimlewisjr
imagecharlotte
azerbaijanazerbaijan
fuera
thrace
gaskets
unknownunknownromania
ragemanchoo
snuggles
antiaustralian
alislamiya
independantly
scmzzzzzzz
consenting
rapidlychangingrapidlydeveloping
meerkatgirluser
tumen
bronte
dialogs
psivalt
angelesdominated
mirifamilies
gayyyyyyyyyyy
opportunists
warmongering
usenet
wikipediaweight
outfielders
dialogo
numeral
thoughtsreccs
almegrahi
fileimgpjpg
beejaypii
jevanyn
lench
mailings
d

relegate
psychogeographic
monaro
homeomorphic
hotness
diria
enthralled
eriksen
kshudrakyah
audaciously
rodnoverie
imutung
uofo
trestarig
bahman
aboslutely
filibusterismoshe
dexter
nrsv
masturbatory
monoid
avails
sponsorship
vaccines
wests
kilometer
nrsc
polynesiarelated
tocopherol
underutilization
geosync
kklllllnnnnnoooo
tsui
arbitrationtkorrovi
overcategorisation
yyyyyyyyyyyyyeeeeeeeeeeaaaaaaaaaaaa
hobbledehoy
abecedarian
proterozoic
tvtropes
fellowtravellers
uncharacteristically
sggs
talkjamesbwatsonaron
millionaire
catcalls
fiz
workplace
editspyl
guttyboyd
tadoussac
gridiron
imagebatbluejpg
allowance
kaputt
mcneightperhaps
bethmannhollweg
koliko
sinhapura
creationmiriam
redtigerxyz
worksitejournaletc
erdem
shigeo
yakimour
collider
collides
raulmacias
suppressant
atall
talkhebron
moistly
incubation
ruddiman
pasteurising
biafra
toadyism
textstratforduponavon
protanakh
auspiciousness
psychodynamic
paedophilia
pointers
readings
ffconsultancycom
vrushali
asnwer
transmogrify
hashtag
cant

khana
naturanaturans
proprtion
khani
khanh
damin
inainte
damir
damit
khans
bsing
morethanape
onslaughts
scribal
lumen
lumea
sourcesorpheus
foufira
norddeutschland
showcylonsthey
enforcement
badgujjars
vigorous
ohhhhhhh
quarry
monotheist
devoutly
crni
monotheism
konfigurationsdatei
hauskalainentom
crna
crne
shaolincom
rayban
deathdate
azteca
commandant
albanoi
orchestrated
immaculate
cdtext
quadruplets
blogosphere
leftennant
false
indianorigin
falsi
falsh
falso
zweierlei
yowiehuntercom
chtito
domestication
pasquinade
atia
srbini
wehewehe
numiswp
doraemon
cuatro
sinatra
atis
teetered
ppppp
pppps
mikasa
bullfrogs
manou
nupedia
manor
manos
standardrachel
nonracist
cipher
unsexy
regressing
manoj
bren
httpapagyifocibhu
wilczekian
placement
bref
bree
bred
brea
javajavascript
sciuromorpha
brey
undersea
brew
realclimate
bret
dist
unverifiability
oldenlandia
notfor
scotts
pageclaudia
statesoas
scotty
thingssohr
scottg
hathigumpha
rubric
pagemodeup
wphtrivia
ghalzai
neodarwinian
trying
itdont
lla

irisholdnorse
uphill
fbb
hightop
crawlers
puffed
mergeable
fuckelwad
wubba
rhynchocystis
fbi
quenching
fbo
homiletic
roadclosedclosedclosedhayle
cnsi
celeborn
wambssgans
tharkuncolldo
yucateco
ducreux
woooooooooooooooooooooooooooooooo
naqshbandi
soke
soka
imageicsdancersjpg
rainfall
ghostwritten
thresholding
natually
nguyen
antilog
quamichan
loadmodulesmodulename
tranh
tubule
kasai
niggas
dmitri
niggaz
trang
politicalimplementational
seguros
disinfection
hhg
diddley
trans
niggah
gravitationally
incetezi
distribuidor
powerball
regals
prabodhananda
gales
originspublishercambridge
userbrianboultontfa
elkeliseti
hedda
galen
nastro
novoselov
teadrinkernewscom
experienceampco
officeholders
nomming
varnishes
breintje
snapdragon
categorygreek
varnished
sabatage
einbrgerung
motorcross
deteriorate
armies
iteam
fastmail
autocollapse
songbook
ballygarvan
eisschildes
harrys
bizzness
thurgood
drastic
wakalaka
malwa
foxsirhistdecemberhtm
aftonbladetisrael
inflicted
michellewell
nakshatra
luchagors
co

lka
uninformative
androzaniamy
kanowna
aditionally
windsurfer
lks
parishesacton
wwwtangallecitycom
acreage
polestars
imageevejpg
notablesignificantspecialwhatever
yourselves
unpoliticallycorrect
gurley
rythum
microbreweries
mauritania
heraldtalkback
sannyasis
mercithnks
meticulously
sekkilar
releaving
bhupi
gitonga
watered
imagepprovjpg
talkastor
sprouse
guber
achumawi
mueren
caudofemoralis
talkredvers
aeristh
dotage
sheol
dysgraphia
pittsburghwestern
wwwshockedorguk
tagetes
hixlord
slavesunreferenced
hillaryhaters
thecodonts
conning
stockbridge
ssjui
senceless
drools
createspace
lesabre
mccray
usermathewignashgutcruncher
radicals
pancake
mccrae
newsmedia
bobdylandiscography
signposted
accredits
bandler
milliard
imagesmalljpg
dvec
lenrcanr
dartmouthians
fasciitis
imagejeansablonalbumjpg
evancho
templateharold
mught
hilltops
exorbitance
foresee
airspace
puella
battuta
tennant
millers
degismis
machiavellianism
tilighman
cronological
preforkmpmfootnotentzliche
kraftwerk
camers
canape
tehs

...

epriotes
mendaliv
bellowed
repaves
phonecalls
fairey
loosened
simian
faires
hellos
foreword
loomis
nonspecialists
theocrat
somehere
nonapnic
subliminal
talbott
imagecosmicomjpg
talbots
envirowacko
moralis
luxemburg
dutchamericans
cadfbcdb
elgato
schefflera
deletionbbwikipediaaarticlesfordeletionfstephanobarberisddafd
komipermyak
alsophila
westfeldzug
cleaning
rockabilly
draconic
yuan
filelinfoxbrandpng
cinderellalike
thnaks
xist
kurdish
reseach
gsr
gst
gsw
wasson
transylvanianardeleanoltean
gsa
angelathielemannrose
gsc
gsb
usermiketwo
gsd
sherri
gsi
gsk
diamagnetic
gsm
gsl
yankees
hotell
wittekind
abstain
puits
chemolithotrophs
derring
bhedachchaiva
intellidynamical
elect
taiwan
pointillism
patriota
abcxyz
rohangku
alexanderjpg
sutlers
crataegus
schoolwork
wikipediareliablesourcesnoticeboardcarlsagansindigochildren
overthrows
sciurinae
categoryhistorism
stein
defies
organistion
whispy
andvery
collaboratively
sherry
overthrown
defied
thingstaulant
witham
brouwerheyting
jermain
valens
wi

znacznie
seasoning
baldfaced
imagesexpistolsjpg
semianglicgermanwestern
anawintaenwiki
stamford
capitalisms
roversintertoto
sererniominkaa
codeproject
ecstaticheres
masood
newottomanist
diskussionantideutschebeanstandeteteile
contoversial
pandiani
nazijew
puppetsissacharoff
shoo
potpolitej
fightingobbler
jacurek
clerk
finetuned
harryboylestime
french
freespeechinbrooklyn
purin
purim
userslipknotanarchy
clery
chomage
victimizes
harmfully
softwares
imageoverthehillsandfarawayjpg
adverting
neibor
besmirching
atmosfrica
canadian
russianness
yapyapyap
namechecking
toraja
plume
placings
ceral
shilpokala
usersecisek
useful
stephenhawkingsuniversecom
stricto
strake
stiletto
vexillologists
conspracyadherent
englishvernacular
schrieb
franck
franci
franco
unfortified
franca
thatto
france
stooges
stenographers
francs
gorringetake
internode
drinkable
antifoxred
obelisk
userbongwarrior
jabalpur
mouthing
matalan
khannaavishkaar
ralitsa
flachteller
rotational
barnstar
gassy
tokyo
deformed
predicatable

involes
eigenen
cayo
euroafro
proisrael
sju
kobus
santalkolhemalhe
marszaek
beduin
bobmarley
cancio
drae
eigenes
finlndare
snak
robsonkanu
textualist
manymany
talkkrbnlast
snag
shapeir
aacsb
takanashi
snap
sinisa
denialists
sinise
chipman
silken
dwarves
akureyri
newspaperarchivecom
lvbtara
pazaristanka
bohemdeb
wikipediatalkwikiprojectnationalbasketballassociationhighlightsininfobox
materialists
trendily
kirkens
moriah
blemish
anitclericalism
imageandrev
imageandrew
nwikipediaorgwikijosephmccabe
youor
brett
transgress
decoherer
dwarven
zvati
nusra
hyevadhigamyante
underdeveloped
insincere
ewwwwwwww
lolcat
destub
taprobanus
cooperator
gundulic
imageschoolpicjpg
jitterbug
mostrar
sentencepropositionstatement
resonances
disputations
charectors
aarp
pucherani
promulgator
oenology
povresearchblack
clifftop
restoftheworld
greenwaldquote
ulayiti
spamwikipedia
nahane
depressions
hispaniclatino
notthing
continuing
costumes
nahani
slorasfe
bigendian
ronastudor
lounges
lounger
costumed
carbide
lo

terminologies
knwatv
wassbosbbrkcin
wikimediawide
persistantley
catnap
timings
fabrizio
kahriger
spanishspeakers
enties
entier
resonance
automaton
navigation
tudorbethan
provocations
rededicate
dippin
synergtique
opprtunity
modifying
gourami
dashiki
artbooks
referitoare
ipecac
squadrons
akibat
pembangunan
quck
alarums
ravage
sneeky
tois
zrazu
coffeebreak
confounder
gotee
wech
gotem
northpng
rostmani
wpnotguide
youavantgarde
mecanismo
cadherincatenin
rumpelstiltskin
regimentsorif
provablegdels
boucher
ahtisaari
suggestarbcom
longitude
senegaleseafrican
interessiert
ferry
sawmills
englishchinese
ejaculator
merchandises
wikipediamanual
trump
nicbase
geklassifiseer
wikipedialink
newlook
hahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahahaha
diebold
laudatenationnet
topchartscom
wiimote
abdusamatov
workin
osmosis
imagenagantcartridgecomparisonjpg


watsons
volksvertegenwoordiging
judaizing
velle
weeping
rigitano
mouscron
admisttraot
chromosone
dxs
largeur
philanderer
causalities
cooperate
sramoenje
faultless
penis
butoh
tuaisceart
paralleled
wtih
squealed
slaps
talkcopyrightsorthodox
slapp
foggiest
annot
ordinals
condominium
radoesht
peopleand
annon
demonically
datebook
denkmal
renomination
sendou
tau
tav
taw
tap
taq
tar
tas
pennines
malloced
tax
profilepdf
taz
dependence
tad
tae
taf
alahram
condescend
ipage
tab
tac
tal
tam
tan
tao
tah
tai
taj
technowikigeek
taylori
legging
fortunato
dependency
microaggressions
dxc
laihdutusmetodi
angantyrs
fortunate
actualities
panim
userrdos
slithered
highpressure
taylors
panic
coniving
trusses
sunheadren
silvicola
pitch
benifit
panarmeniannet
cryokinesis
discomfort
southerneuropean
murderforhire
flamethrowerfreezergas
sahaba
lobsterthermidor
skullduggery
milleniums
forumfansiteblog
semitones
defaultsortlautman
khosrow
electionbyelection
swamiji
brushes
imagekarangillanjpg
windpower
therearound